In [1]:
%load_ext autoreload
%autoreload 2

import os
import sys
sys.path.insert(0, "biotrainer")
import optuna
from biotrainer.protocols import Protocol
from biotrainer.utilities.cli import train

/Users/janleusch/anaconda3/envs/biotrainer/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [7]:
config = {
    "input_file": "../../../data/sampled_3Dii.fasta",
    "protocol": Protocol.residue_to_class.name,
    "model_choice": "FNN",
    "device": "mps",
    "optimizer_choice": "adam",
    "learning_rate": 1e-3,
    "loss_choice": "cross_entropy_loss",
    "num_epochs": 200,
    "batch_size": 128,
    "patience": 3,
    "ignore_file_inconsistencies": True,
    "cross_validation_config": {
        "method": "hold_out"
    },
    "embeddings_file": "../../../output/residue_to_class/ProstT5/embeddings_file_ProstT5.h5",
    #"embedder_name": "RostLab/ProstT5",
    "model_params": {
            "dropout_rate": 0.15,
            "n_layers": 3,
            "kernel_sizes": [(7, 1), (7, 1), (5, 1)],
            "padding": [(3, 0), (3, 0), (2, 0)],
            "hidden_dims": [256, 32]
    },
}

In [3]:
def objective_CNN(trial):
    config.copy()
    config["output_dir"] = f"optuna_results/{trial.number}"

    learning_rate = trial.suggest_float("learning_rate", 1e-5, 1e-2, log=True)
    config["learning_rate"] = learning_rate

    dropout_rate = trial.suggest_float("dropout_rate", 0.1, 0.5)
    n_layers = trial.suggest_int("n_layers", 1, 3)
    kernel_sizes = [(trial.suggest_categorical(f"kernel_size_{i}", [3, 5, 7]), 1) for i in range(n_layers)]
    padding = [(k[0] // 2, 0) for k in kernel_sizes]
    hidden_dims = [trial.suggest_int(f"hidden_dim_{i}", 32, 512) for i in range(n_layers-1)]
    last_layer_FNN = False # trial.suggest_categorical("last_layer_FNN", [True, False])

    config["model_params"] = {
        "dropout_rate": dropout_rate,
        "kernel_sizes": kernel_sizes,
        "padding": padding,
        "hidden_dims": hidden_dims,
        "last_layer_FNN": last_layer_FNN # for now the masking is not working with FNN as last layer
    }

    print(config)
    res = train(config)
    return res["training_results"]["hold_out"]["best_training_epoch_metrics"]["training"]["accuracy"]

In [4]:
def objective_FNN(trial):
    config.copy()
    config["output_dir"] = f"optuna_results/{trial.number}"

    learning_rate = trial.suggest_float("learning_rate", 1e-5, 1e-2, log=True)
    config["learning_rate"] = learning_rate

    dropout_rate = trial.suggest_float("dropout_rate", 0.1, 0.5)
    n_layers = trial.suggest_int("n_layers", 1, 3)
    hidden_dims = [trial.suggest_int(f"hidden_dim_{i}", 32, 512) for i in range(n_layers-1)]
    
    config["model_params"] = {
        "dropout_rate": dropout_rate,
        "hidden_dims": hidden_dims
    }

    res = train(config)
    return res["training_results"]["hold_out"]["best_training_epoch_metrics"]["training"]["accuracy"]

In [5]:
os.makedirs("optuna_trials", exist_ok=True)
storage = f'sqlite:///optuna_trials/study.db'

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(study_name="3Dii",
                            direction="maximize", 
                            sampler=sampler, 
                            storage=storage, 
                            load_if_exists=True)

[I 2025-08-12 15:35:37,916] A new study created in RDB with name: 3Dii


In [ ]:
study.optimize(objective_FNN, n_trials=1)

''

In [41]:
study.best_trial

FrozenTrial(number=4, state=1, values=[0.5685243010520935], datetime_start=datetime.datetime(2025, 8, 11, 14, 9, 14, 485260), datetime_complete=datetime.datetime(2025, 8, 11, 15, 2, 39, 923205), params={'learning_rate': 0.000918391052072852, 'dropout_rate': 0.20172967629806815, 'n_layers': 2, 'kernel_size_0_1': 3, 'kernel_size_1_1': 5, 'hidden_dim_0': 123}, user_attrs={}, system_attrs={}, intermediate_values={}, distributions={'learning_rate': FloatDistribution(high=0.01, log=True, low=1e-05, step=None), 'dropout_rate': FloatDistribution(high=0.5, log=False, low=0.1, step=None), 'n_layers': IntDistribution(high=3, log=False, low=1, step=1), 'kernel_size_0_1': IntDistribution(high=7, log=False, low=3, step=1), 'kernel_size_1_1': IntDistribution(high=7, log=False, low=3, step=1), 'hidden_dim_0': IntDistribution(high=512, log=False, low=32, step=1)}, trial_id=4, value=None)

In [7]:
res = train(config)

''

{'device': device(type='mps'), 'seed': 42, 'save_split_ids': False, 'sanity_check': True, 'ignore_file_inconsistencies': False, 'external_writer': 'tensorboard', 'output_dir': PosixPath('/Users/janleusch/Documents/phd/biotrainer/output'), 'bootstrapping_iterations': 30, 'validate_input': True, 'input_file': '/Users/janleusch/Documents/phd/biotrainer/data/sampled_3Dii.fasta', 'optimizer_choice': 'adam', 'learning_rate': 0.001, 'epsilon': 0.001, 'loss_choice': 'cross_entropy_loss', 'model_params': {'dropout_rate': 0.15, 'n_layers': 3, 'kernel_sizes': [(7, 1), (7, 1), (5, 1)], 'padding': [(3, 0), (3, 0), (2, 0)], 'hidden_dims': [256, 32]}, 'num_epochs': 200, 'batch_size': 128, 'patience': 10, 'shuffle': True, 'use_class_weights': False, 'auto_resume': False, 'limited_sample_size': -1, 'embedder_name': 'one_hot_encoding', 'use_half_precision': False, 'cross_validation_config': {'method': 'hold_out', 'choose_by': 'loss'}, 'log_dir': '/Users/janleusch/Documents/phd/biotrainer/output/CNN/one_

{'device': device(type='mps'), 'seed': 42, 'save_split_ids': False, 'sanity_check': True, 'ignore_file_inconsistencies': False, 'external_writer': 'tensorboard', 'output_dir': PosixPath('/Users/janleusch/Documents/phd/biotrainer/output'), 'bootstrapping_iterations': 30, 'validate_input': True, 'input_file': '/Users/janleusch/Documents/phd/biotrainer/data/sampled_3Dii.fasta', 'optimizer_choice': 'adam', 'learning_rate': 0.001, 'epsilon': 0.001, 'loss_choice': 'cross_entropy_loss', 'model_params': {'dropout_rate': 0.15, 'n_layers': 3, 'kernel_sizes': [(7, 1), (7, 1), (5, 1)], 'padding': [(3, 0), (3, 0), (2, 0)], 'hidden_dims': [256, 32]}, 'num_epochs': 200, 'batch_size': 128, 'patience': 10, 'shuffle': True, 'use_class_weights': False, 'auto_resume': False, 'limited_sample_size': -1, 'embedder_name': 'one_hot_encoding', 'use_half_precision': False, 'cross_validation_config': {'method': 'hold_out', 'choose_by': 'loss'}, 'log_dir': '/Users/janleusch/Documents/phd/biotrainer/output/CNN/one_

In [23]:
res["training_results"]["hold_out"]["best_training_epoch_metrics"]["training"]["accuracy"]

0.20687341690063477